# Hafta 5: Sürekli Entegrasyon (CI) ile Pipeline Otomasyonu

**Dersin Hedefleri:**
1.  Sürekli Entegrasyon (Continuous Integration - CI) kavramını ve MLOpstaki rolünü anlamak.
2.  CI'ın temel faydalarını (hızlı geri bildirim, artan kalite, azalan risk) kavramak.
3.  **GitHub Actions** kullanarak basit bir CI iş akışı (workflow) oluşturmak.
4.  Oluşturulan iş akışının, kodda yapılan her değişiklikte otomatik olarak çalışmasını sağlamak.
5.  CI pipeline'ına kod stili kontrolü (linting) ve testleri (pytest) otomatik olarak dahil etmek.

## 1. Sürekli Entegrasyon (CI) Nedir?

Sürekli Entegrasyon, birden fazla geliştiricinin üzerinde çalıştığı bir projede, kod değişikliklerinin düzenli olarak (genellikle günde birden çok kez) merkezi bir repository'ye entegre edildiği bir yazılım geliştirme pratiğidir. Her entegrasyon, otomatik bir "build" ve "test" süreci tarafından doğrulanır.

**Veri Bilimi için CI'ın Anlamı:**

Bir takım üyesi, `git push` komutuyla kodunu GitHub'a gönderdiğinde veya bir Pull Request açtığında, bir sunucu otomatik olarak şunları yapar:
- Kodun bir kopyasını indirir.
- Gerekli kütüphaneleri kurar.
- **Kod stili kontrolü (Linting)** yapar: Kodun belirli bir stil standardına (örn: PEP8) uygun olup olmadığını denetler.
- **Testleri çalıştırır:** Hafta 2'de yazdığımız tüm `pytest` testlerini çalıştırarak hiçbir şeyin bozulmadığını doğrular.

Eğer bu adımlardan herhangi biri başarısız olursa, CI pipeline'ı durur ve geliştiriciye anında geri bildirim verir. Bu, hataların çok erken bir aşamada yakalanmasını sağlar.

## 2. GitHub Actions ile Tanışma

**GitHub Actions**, CI/CD süreçlerini doğrudan GitHub repository'niz içinde otomatikleştirmeyi sağlayan bir platformdur. İş akışları (workflows), projenizin kök dizinindeki `.github/workflows/` klasöründe bulunan `YAML` dosyaları ile tanımlanır.

**Temel GitHub Actions Kavramları:**

- **Workflow (İş Akışı):** Belirli bir olaya (event) tepki olarak çalışan, otomatize edilmiş süreç. Bir YAML dosyası bir workflow'u temsil eder.
- **Event (Olay):** Bir workflow'u tetikleyen aktivite. Örnekler: `push` (bir branch'e kod gönderildiğinde), `pull_request` (bir PR açıldığında veya güncellendiğinde).
- **Job (İş):** Bir workflow içindeki görevler bütünü. Job'lar paralel veya sıralı çalışabilir.
- **Step (Adım):** Bir job içindeki en küçük yürütme birimi. Bir komut çalıştırmak veya bir "action" (hazır bir görev paketi) kullanmak olabilir.
- **Runner:** Workflow'u çalıştıran sunucu. GitHub, Linux, Windows ve macOS için sanal makineler sağlar.

## 3. Pratik Uygulama: İlk CI Workflow'umuzu Oluşturma

Bu bölümde, Hafta 2'de oluşturduğumuz proje yapısı için bir CI pipeline'ı tasarlayacağız. Bu uygulama, pratik olarak bir metin editörü ve terminal kullanılarak yapılır, ancak süreci burada Python script'leri ile simüle edeceğiz.

**Proje Yapımız:**
```
.
├── .github/
│   └── workflows/
│       └── python-ci.yml   <-- Workflow dosyamız
├── src/
│   ├── __init__.py
│   └── data_cleaning.py
├── tests/
│   ├── __init__.py
│   └── test_data_cleaning.py
└── requirements.txt        <-- Gerekli kütüphaneler
```

### Adım 1: Gerekli Dosyaları Oluşturma

Önce, projemizin ihtiyaç duyduğu kütüphaneleri listeleyen bir `requirements.txt` dosyası oluşturalım.

In [ ]:
import os
import yaml
import shutil

# --- Proje Ortamını Hazırlama ---
project_root = "hafta5_projesi"
if os.path.exists(project_root):
    shutil.rmtree(project_root)

# Önceki haftalardaki gibi klasörleri ve dosyaları oluşturalım
src_dir = os.path.join(project_root, "src")
tests_dir = os.path.join(project_root, "tests")
os.makedirs(src_dir)
os.makedirs(tests_dir)
open(os.path.join(src_dir, "__init__.py"), 'w').close()
open(os.path.join(tests_dir, "__init__.py"), 'w').close()

# Hafta 2'deki kodlarımız
with open(os.path.join(src_dir, "data_cleaning.py"), "w") as f:
    f.write("""
import pandas as pd
import numpy as np
def clean_patient_data(df: pd.DataFrame) -> pd.DataFrame:
    df_copy = df.copy()
    df_copy.loc[df_copy['age'] < 0, 'age'] = np.nan
    return df_copy
""")

with open(os.path.join(tests_dir, "test_data_cleaning.py"), "w") as f:
    f.write("""
import pytest
import pandas as pd
from src.data_cleaning import clean_patient_data
def test_clean_patient_data_removes_negative_age():
    dirty_data = pd.DataFrame({'age': [34, -5, 45]})
    cleaned_data = clean_patient_data(dirty_data)
    assert (cleaned_data['age'] >= 0).all() or cleaned_data['age'].isnull().all()
""")

# --- `requirements.txt` Oluşturma ---
requirements_content = """
pandas
numpy
pytest
flake8
"""
with open(os.path.join(project_root, "requirements.txt"), "w") as f:
    f.write(requirements_content)
print(f"'requirements.txt' oluşturuldu.")

### Adım 2: Workflow YAML Dosyasını Oluşturma

Şimdi en önemli kısım olan `.github/workflows/python-ci.yml` dosyasını oluşturalım. Bu dosya, GitHub'a ne yapacağını söyleyen talimatları içerir.

In [ ]:
# --- Workflow Klasörünü ve Dosyasını Oluşturma ---
workflow_dir = os.path.join(project_root, ".github", "workflows")
os.makedirs(workflow_dir)

# YAML içeriğini bir Python dictionary olarak tanımlayalım
ci_workflow_dict = {
    'name': 'Python CI Workflow',
    
    # Ne zaman çalışacak? `main` branch'ine push yapıldığında VEYA bir PR açıldığında.
    'on': {
        'push': {'branches': ['main']},
        'pull_request': {'branches': ['main']}
    },
    
    'jobs': {
        'build-and-test': {
            'runs-on': 'ubuntu-latest', # Hangi işletim sisteminde çalışacak?
            'steps': [
                # Adım 1: Kodu indir (checkout)
                {
                    'name': 'Check out repository code',
                    'uses': 'actions/checkout@v3'
                },
                # Adım 2: Python'ı kur
                {
                    'name': 'Set up Python 3.9',
                    'uses': 'actions/setup-python@v3',
                    'with': {
                        'python-version': '3.9'
                    }
                },
                # Adım 3: Bağımlılıkları kur
                {
                    'name': 'Install dependencies',
                    'run': """
                    python -m pip install --upgrade pip
                    pip install -r requirements.txt
                    """
                },
                # Adım 4: Linting (Kod stili kontrolü)
                {
                    'name': 'Lint with flake8',
                    'run': 'flake8 src tests'
                },
                # Adım 5: Testleri çalıştır
                {
                    'name': 'Run tests with pytest',
                    'run': 'pytest'
                }
            ]
        }
    }
}

# Python dictionary'sini YAML formatında dosyaya yaz
with open(os.path.join(workflow_dir, "python-ci.yml"), "w") as f:
    yaml.dump(ci_workflow_dict, f, default_flow_style=False, sort_keys=False)

print(f"'{os.path.join(workflow_dir, 'python-ci.yml')}' oluşturuldu.")

# YAML dosyasının içeriğini de görelim
with open(os.path.join(workflow_dir, "python-ci.yml"), 'r') as f:
    print("\n--- YAML Dosya İçeriği ---")
    print(f.read())
    
# Temizlik
shutil.rmtree(project_root)

### Süreç Nasıl İşler?

1.  Yukarıda oluşturulan dosya yapısını yerel `git` repository'nize commit'lersiniz.
2.  Bu commit'i `git push origin main` komutu ile GitHub'daki remote repository'nize gönderirsiniz.
3.  GitHub, `.github/workflows` klasöründe yeni bir YAML dosyası olduğunu algılar ve `push` olayını tetikler.
4.  GitHub Actions, bir `ubuntu-latest` runner'ı (sanal makine) başlatır.
5.  Runner, YAML dosyasındaki `steps` altında belirtilen adımları sırayla yürütür:
    *   Kodunuzu sanal makineye indirir.
    *   Python 3.9'u kurar.
    *   `requirements.txt` içindeki `pandas`, `pytest`, `flake8` gibi kütüphaneleri kurar.
    *   `flake8` ile kodunuzun stilini denetler. Bir hata bulursa (örn. kullanılmayan import), pipeline burada durur ve başarısız olur.
    *   `pytest` komutunu çalıştırarak tüm testlerinizi yürütür. Bir test başarısız olursa, pipeline burada durur ve başarısız olur.
6.  Tüm adımlar başarılı olursa, pipeline "başarılı" (yeşil tik) olarak işaretlenir. Başarısız olursa "başarısız" (kırmızı çarpı) olarak işaretlenir.

Sonucu, GitHub repository'nizdeki "Actions" sekmesinden canlı olarak takip edebilirsiniz.

### Alıştırma: CI Pipeline'ını Başarısız Hale Getirme

Gerçek bir geliştirme senaryosunu deneyimlemek için CI pipeline'ını kasten bozalım.

1.  Yerel projenizde `tests/test_data_cleaning.py` dosyasını açın.
2.  Mevcut testi, kesinlikle başarısız olacak bir `assert` ifadesi ekleyerek değiştirin. Örneğin:
    ```python
    def test_clean_patient_data_removes_negative_age():
        assert 1 == 2 # Bu test kesinlikle başarısız olacak
    ```
3.  Bu değişikliği commit'leyin ve GitHub'a `push`'layın.
4.  GitHub'daki "Actions" sekmesine gidin ve yeni başlayan workflow'u izleyin.
5.  "Run tests with pytest" adımında pipeline'ın hata vererek durduğunu ve kırmızı bir çarpı ile işaretlendiğini gözlemleyin. Hata detaylarına tıklayarak `pytest`'in hangi `assert` ifadesinde başarısız olduğunu görebilirsiniz.
6.  Hatayı düzeltin, tekrar commit'leyip push'layın ve pipeline'ın bu sefer başarılı (yeşil tik) olduğunu görün.

### Haftanın Özeti

Bu hafta, projelerimize profesyonel bir kalite güvence katmanı ekledik.

- **Sürekli Entegrasyon (CI)**, hataları erken yakalamak ve kod kalitesini sürekli yüksek tutmak için vazgeçilmez bir pratiktir.
- **GitHub Actions**, bu otomasyonu doğrudan kodumuzun yaşadığı yerde, kolayca yapılandırmamızı sağlar.
- Bir CI pipeline'ı, kod stili kontrolü (linting) ve otomatik testler gibi adımları içermelidir.
- Başarılı bir CI süreci, bir projenin "sağlıklı" olduğunun en önemli göstergelerinden biridir.

### Sonraki Adımlar

Projemiz artık versiyon kontrollü, test edilebilir ve kalite kontrolü otomatize edilmiş durumda. Bu, bir modeli üretime almak için gereken sağlam altyapıdır. Bir sonraki hafta, **Hafta 6: Model Dağıtım Stratejileri**'nde, Hafta 4'te `MLflow` ile kaydettiğimiz bir modeli, dış dünyanın kullanabileceği bir API servisine nasıl dönüştüreceğimizi ve bunu `Docker` ile nasıl paketleyeceğimizi öğreneceğiz.

---

## **Hafta 6: Model Dağıtım Stratejileri (API & Konteynerler)**
```python